Here is a list of all functions used in the provided code along with their descriptions:

1. **saveToBucket(modelName, bucketName, objectName):** This function saves a provided model to an AWS S3 bucket. It uses the 'boto3' library to interact with AWS services.

2. **loadFromBucket(bucketName, objectName):** This function retrieves a model from an AWS S3 bucket and loads it into the current workspace.

3. **assembleDF(ticker):** This function retrieves historical stock data for a given ticker symbol using the Finnhub API, cleans the data, and saves it as a pandas DataFrame.

4. **assembleModel(df):** This function prepares the environment for model training using the Pycaret library and then creates an ARIMA model based on the provided DataFrame. 

5. **saveModel(model):** This function saves a trained model object into the current working directory as a pickle file.

6. **loadModel(modelPath):** This function loads a pre-trained model from a pickle file.

7. **predictModel(days, model):** This function finalizes a provided model and generates predictions for the specified number of days.

8. **graphPredictionModel(ticker):** This function retrieves historical data, trains a model, generates predictions, and plots the predictions along with the historical data.

9. **getResiduals(ticker):** This function returns a DataFrame containing the residuals for each prediction from the model. It achieves this by training the model on a portion of the data, then testing on the rest and recording the difference between actual and predicted values (residuals).

10. **processResiduals(filePath):** This function processes the residuals from the backtester. It is currently empty and needs to be implemented.

11. **getTrades(ticker):** This function determines trading signals (buys and sells) based on model predictions, saves these signals along with their time indices into several dictionaries, and finally saves these dictionaries as a CSV file.

12. **processTrades(filename):** This function calculates the total profit and tax from the trades made by the trading algorithm. It reads trades from a provided CSV file and processes the data accordingly.

13. **graphTradeData(tradeFileName, ticker):** This function plots buy and sell points on a graph of the historical data. It reads trades from a provided CSV file and overlays these trades on a plot of the historical data for the given ticker symbol.


In [6]:
!pip install finnhub-python
!pip install pandas 
!pip install matplotlib
!pip install boto3
!pip install datetime

In [7]:
!pip install --no-cache-dir --force-reinstall --ignore-installed pycaret[full]
!pip install packaging

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 79.9/79.9 MB 190.0 MB/s eta 0:00:0000:0100:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.7/1.7 MB 114.5 MB/s eta 0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Installing backend dependencies ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 11.8/11.8 MB 204.3 MB/s eta 0:00:00a 0:00:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 61.2/61.2 kB 275.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 12.1/12.1 MB 194.8 MB/s eta 0:00:00a 0:00:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 160.5/160.5 kB 215.3 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 106.8/106.8 kB 318.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 9.6/9.6 MB 211.0 MB/s eta 0:00:00a 0:00:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 34.4/34.4 MB 231.7 MB/s eta 0:00:00a 0:00:01
     ━━━

In [1]:
'''
Function to calculate a given number of days in unix
'''
def getUnix(days):
    return days * 86400

In [2]:
import boto3
import pickle
'''
save model to s3 bucket
'''
def saveToBucket(modelName, bucketName, objectName):
    s3 = boto3.client('s3')
    try:
        s3.put_object(
            Body=pickle.dumps(modelName),
            Bucket=bucketName,
            Key=objectName
        )
        print(f"ARIMA model saved as '{object_key}' in '{bucket_name}'.")
    except Exception as e:
        print(f"Error saving ARIMA model to S3: {str(e)}")
    return

In [3]:
import requests
import json
import pandas as pd

def assembleDF(ticker):
    accessKey = "21ecc4ec89881af0511ee1d5072664ad"
    #accessKey = "1abe60bea1b33585a521e867fe6300da"
    #accessKey = "1de00dd745a0a45c6443f2da6b8c50f9"
    paginationLimit = 1000
    url = f"http://api.marketstack.com/v1/eod?access_key={accessKey}&symbols={ticker}&date_from=2020-01-13&date_to=2024-01-01&limit={paginationLimit}"
    r = requests.get(url)
    data = json.loads(r.text)
    data = data.get('data')
    dfData = {}
    for row in data:
        index = row.get('date').split('T')[0]
        dfData[index] = row.get('adj_close')
    df = pd.DataFrame.from_dict(dfData, orient="index", columns=['c'])
    df.index = pd.to_datetime(df.index)
    df = df.asfreq(freq='d')
    df['c'] = df['c'].ffill()
    df.index.freq = 'D'
    return df

spy = assembleDF("SPY")

In [4]:
'''
Function to combine multiple dataframes representing consecutive time series data
'''
def combineDF(frames):
    dfList = []
    for frame in frames:
        df = pd.read_csv(frame)
        dfList.append(df)
    result = pd.concat(dfList)
    return result 
#frames = ['CVXbacktestData0.csv', 'CVXbacktestData1.csv', 'CVXbacktestData2.csv', 'CVXbacktestData3.csv', 'CVXbacktestData4.csv']
#df = combineDF(frames)
#df.to_csv('CVXbackTestData')

In [5]:
from pycaret.time_series import * 
'''
Setup Pycaret framework and determine which model best suits the data
'''
def assembleModel(df):
    df = df.asfreq(freq='d')
    df.index.freq = 'D'
    df['c'] = df['c'].ffill()
    setup(df, fh=5, session_id=123)
    #best = compare_models()
    best = create_model('arima')
    result = best
    return result

In [6]:
'''
Generate predictions based on the best model
'''
def predictModel(days, model):
    model = finalize_model(model)
    prediction = predict_model(model, fh=days)
    print(prediction)
    return prediction

In [7]:
import matplotlib.pyplot as plt
import matplotlib.dates as mdates
'''
Function to graph the prediction model
'''
def graphPredictionModel(ticker):
    historicalData = assembleDF(ticker)
    model = assembleModel(historicalData)
    predictionModel = predictModel(10, model)
    predictionModel.index = predictionModel.index.to_timestamp()
    df = pd.concat([historicalData, predictionModel['y_pred']], axis=0)
    plt.figure(figsize=(100, 6))
    plt.plot(df.index, df.values)
    plt.gca().xaxis.set_major_locator(mdates.MonthLocator())
    plt.xlabel('Time')
    plt.ylabel('Price')
    plt.title(f'{ticker} price with predictions')
    plt.xticks(rotation=45)
    plt.show()


In [8]:
'''
Returns a pandas DataFrame containing the residuals for each prediction with the corresponding time index
This function functions as a backtester
'''
def getResiduals(ticker):
    data = pd.DataFrame(assembleDF(ticker))
    cutoff = int(0.7 * len(data))
    trainingData = data[:cutoff]
    testingData = data[cutoff:]
    residuals = []
    residualsIndex = []
    for index, value in testingData.itertuples():
        model = assembleModel(trainingData)
        # predict the value 
        prediction = predictModel(1, model)
        # record the residual
        predictedPrice = prediction.iloc[0]['y_pred']
        residual = value - predictedPrice
        residuals.append(residual)
        residualsIndex.append(index)
        # add the test row to the training data
        trainingData.loc[index] = value
    result = pd.DataFrame(residuals, index=residualIndex, columns=['Residual'])
    result.to_csv('residuals.csv', index_label='Date')
    print(residuals)
    print(result)
    return result
#getResiduals('AAPL')

In [9]:
'''
Function to process the list of residuals collected in the backtester
'''
def processResiduals(filePath):
    df = pd.read_csv(filePath)
    #read through this dataframe
    #draw test statistics to show accuracy of algorithms predictions using residual data

In [10]:
"""
Samia approved backtests
"""
def officialBackTests(ticker):
    data = pd.DataFrame(assembleDF(ticker))
    cutoff = int(0.5 * len(data))
    trainingData = data[:cutoff]
    testingData = data[cutoff:]
    accuracy = 0
    timePeriod = 5
    count = 0
    for index, value in testingData.itertuples():
        if count % timePeriod == 0:
            model = assembleModel(trainingData)
            # predict the value 
            prediction = predictModel(timePeriod, model)
            # record the residual
            predictedPrice = prediction.iloc[timePeriod - 1]['y_pred']
            currentPrice = trainingData.iloc[-1]['c']
            predictedDirection = predictedPrice - currentPrice
            actualDirection = value - currentPrice
            check = predictedDirection * actualDirection
            if check > 0:
                accuracy += 1
            else:
                print(index,end=": ")
                print(value)
            trainingData.loc[index] = value
        count += 1
    accuracy /= len(testingData)
    accuracy *= timePeriod
    return accuracy * 100
#print(officialBackTests("TSLA"))
        

# GPT MODEL
#### Credits to Julia for this code

In [11]:
!pip install openai==0.28 requests yfinance alpaca-trade-api

In [11]:
news_api_key = "PK1SX2TK4RE2U1KSUNS8"
secret = "t1pm9Sk1TUsRtxVqNYAo6V9W9FeZ0TbAwTBYTw0f"
endpoint = 'https://data.alpaca.markets'

In [12]:
def get_percent_change(old_value, new_value):
    """
    Calculate the percent change between two values.

    Args:
        old_value (float): The initial value.
        new_value (float): The final value.

    Returns:
        float: The percent change, as a decimal.
    """
    if old_value == 0:
        return None  # Avoid division by zero
    percent_change = ((new_value - old_value) / abs(old_value)) * 100.0
    return percent_change

In [13]:
import json
import requests
#import pkg_resources
#pkg_resources.require("Openai==0.28")
import openai 
import yfinance as yf
from datetime import datetime, timedelta, time
import pandas as pd
import os
from alpaca_trade_api import REST, Stream

rest_client = REST(news_api_key, secret)
openai.api_key = "XXX"
openai.api_base = "https://expertsys1.openai.azure.com/" # your endpoint should look like the following https://YOUR_RESOURCE_NAME.openai.azure.com/
openai.api_type = 'azure'
openai.api_version = '2023-05-15' # this may change in the future
deployment_name='expertsys1' #This will correspond to the custom name you chose for your deployment when you deployed a model.

"""
Function to handle the GPT model.
Args:
    ticker: the ticker to analyze 
    d1: datetime argument --> IE: datetime(yyy, mm, dd)
    d1: datetime argument --> IE: datetime(yyy, mm, dd)
"""
def runGPT(ticker, d1, d2):
    #prev_day = datetime(2023, 11, 23)
    #prev2_day = datetime(2023, 11, 22)
    prev_day = d1
    prev2_day = d2
    # Get random past dates
    today = datetime.now()
    desired_time = datetime.now().time()
    pull_day = datetime.combine(today, desired_time)
    headlines=[]
    day0 = today
    #price_open[2] = yf.download(ticker, pull_day)['Open'][0]
    # Search for news articles related to the stock
    articles = rest_client.get_news(ticker, prev2_day.strftime('%Y-%m-%d'), prev_day.strftime("%Y-%m-%d"))
    # Extract headlines from the articles
    headlines = [x.headline for x in articles]
    user_message = f"""Forget all your previous instructions. Pretend you are a financial expert. You are
        a financial expert with stock recommendation experience. Provide a prediction for the direction of the stock,
        using only 1 word, 'bullish' for a positive trend, 'bearish' for a negative trend, or 'n/a' 
        if there is no headline provided or any other exception. Only respond with 'bullish' or 'bearish' if  the headlines
        could have a significant impact on the stock price, otherwise say 'n/a'. Do not respond with anything other than
        one of these words. 
        Are these headlines good or bad for the stock price of {ticker} 
        in the next five days?
        Headline: ${headlines}"""
    response = openai.ChatCompletion.create(
        engine=deployment_name,
        messages=[{"role": "system", "content": user_message}],
        max_tokens=500
    )
    assistant_response = response['choices'][0]['message']['content']
    if (assistant_response == None):
        return 'n/a'
    return assistant_response

In [14]:
def gptModel(ticker, d1, d2):
    rest_client = REST(news_api_key, secret)
    openai.api_key = "XXX"
    openai.api_base = "https://expertsys1.openai.azure.com/" # your endpoint should look like the following https://YOUR_RESOURCE_NAME.openai.azure.com/
    openai.api_type = 'azure'
    openai.api_version = '2023-05-15' # this may change in the future
    deployment_name='expertsys1' #This will correspond to the custom name you chose for your deployment when you deployed a model.
    result = runGPT(ticker, d1, d2)
    return result

ticker = 'AAPL'
check = gptModel(ticker, datetime(2024, 1, 2), datetime(2024, 1, 1))
print(check)

bullish


# INTEGRATED MODEL

In [15]:
from datetime import datetime, timedelta

def parseDate(date, timePeriod):
    y = int(date[0])
    m = int(date[1])
    d = int(date[2])
    # Check if timePeriod is within the specified range
    if not (0 < timePeriod < 31):
        raise ValueError("Invalid timePeriod. It must be > 0 and < 31.")
    month_days = {
        '1': 31,
        '2': 28,
        '3': 31,
        '4': 30,
        '5': 31,
        '6': 30,
        '7': 31,
        '8': 31,
        '9': 30,
        '10': 31,
        '11': 30,
        '12': 31
    }
    if d - timePeriod > 0:
        print("hhh")
        return datetime(y, m, d - timePeriod)
    elif d - timePeriod <= 0:
        remaining_days = timePeriod - d
        if m - 1 > 0:
            print("jjj")
            return datetime(y, m - 1, month_days[str(m - 1)] - remaining_days)
        else:
            # If the current month is January, go back to December of the previous year
            print("ppp")
            return datetime(y - 1, 12, month_days['12'] - remaining_days)

In [16]:
"""
Returns:
    1: Bullish
    -1: Bearish
    0: Uncertain
"""
def integratedModelLogic(gptDecision, arimaDecision):
    gptDecision = gptDecision.lower()
    gptDecision = gptDecision.replace(".", "")
    print(f"checkDecisionString; {gptDecision}")
    gptDecisions = {'bearish': -1, 'bullish': 1, 'n/a': 0}
    gptDecision = gptDecisions.get(gptDecision)
    check = arimaDecision * gptDecision
    if check > 0:
        # Models agree
        if gptDecision == -1:
            return -1
        else:
            return 1
    elif check < 0:
         # Differing opinions and niether suggests HOLD, look to GPT prediction
        return 0
    elif check == 0:
        return 0

In [17]:
def buildIntegratedBacktestCSV(holdCount, bullCount, bearCount, accuracy, accurateBullCount, accurateBearCount, testLength,
                              filename):
    if bullCount == 0:
        bullCount = 1
    if bearCount == 0:
        bearCount = 1
    data = [{"Hold Count": holdCount, "Bull Count": bullCount, "Bear Count": bearCount, "Accuracy": accuracy, "Test Length": testLength,
            "Bull Accuracy": accurateBullCount / bullCount, "Bear Accuracy": accurateBearCount / bearCount}]
    df = pd.DataFrame(data)
    df.to_csv(f"{filename}.csv", index=False)
    print(f"file saved as {filename}.csv")

In [18]:
"""
Backtest following Samia's format for the integrated model.
"""
def integratedModelBacktest(ticker):
    data = pd.DataFrame(assembleDF(ticker))
    cutoff = int(0.5 * len(data))
    trainingData = data[:cutoff]
    testingData = data[cutoff:]
    timePeriod = 1
    iterCount = 0
    #### Initialize stats here 
    holdCount = 0
    bullCount = 0
    bearCount = 0
    accuracy = 0
    accurateBullCount = 0
    accurateBearCount = 0
    accurateHoldCount = 0
    testLength = (len(testingData)) / timePeriod
    ### 
    for index, value in testingData.itertuples():
        if iterCount % timePeriod == 0:
            try:
                arimaModel = assembleModel(trainingData)
                # predict the value 
                prediction = predictModel(timePeriod, arimaModel)
                # record the residual
                predictedPrice = prediction.iloc[timePeriod - 1]['y_pred']
                currentPrice = trainingData.iloc[-1]['c']
                arimaDirection = predictedPrice - currentPrice
                ### how to meter the GPT model's assessment as good or bad?
                currDateIndex = str(index).replace("00:00:00","")
                currDate = currDateIndex.split("-")
                d1 = parseDate(currDate, 1)
                d2 = parseDate(currDate, 2)
                gpt_model = gptModel(ticker, d1, d2)
                print(arimaDirection)
                predictedDirection = integratedModelLogic(gpt_model, arimaDirection)
                ###
                actualDirection = value - currentPrice
                check = predictedDirection * actualDirection
                ### Tally bulls and bears
                if predictedDirection > 0:
                    bullCount += 1
                elif predictedDirection < 0:
                    bearCount += 1
                elif predictedDirection == 0:
                    holdCount += 1
                ### Tally Accuracy
                if check >= 0:
                    accuracy += 1
                    if predictedDirection > 0:
                        accurateBullCount += 1
                    elif predictedDirection < 0:
                        accurateBearCount += 1
                trainingData.loc[index] = value
            except TypeError:
                print("TypeError")
                continue
        iterCount += 1
    accuracy /= testLength
    accuracy *= 100
    buildIntegratedBacktestCSV(holdCount, bullCount, bearCount, accuracy, accurateBullCount, accurateBearCount, testLength, ticker)
    return accuracy

# Small Cap Stocks
# small_cap_tickers = ['TWLO', 'ETSY']
# smalls=[]
mids=[]
large=[]
# Mid Cap Stocks
#mid_cap_tickers = ['WEN', 'ZS', 'CRWD', 'DOCU', 'AMED', 'BYND', 'DDOG']

# Large Cap Stocks
large_cap_tickers =  ['JPM', 'NVDA']
# for ticker in small_cap_tickers:
#     result = (integratedModelBacktest(ticker))
#     smalls.append(result)
#     print(result)
# for ticker in mid_cap_tickers:
#     result = (integratedModelBacktest(ticker))
#     mids.append(result)
#     print(result)

for ticker in large_cap_tickers:
    result = (integratedModelBacktest(ticker))
    large.append(result)
    print(result)

              y_pred
2023-07-10  142.4379
hhh
hhh
0.03330000000002542
checkDecisionString; n/a


             y_pred
2023-07-11  142.854
hhh
hhh
-0.3497999999999877
checkDecisionString; n/a


              y_pred
2023-07-12  144.8273
hhh
hhh
-0.6159999999999854
checkDecisionString; bearish


              y_pred
2023-07-13  147.0451
hhh
hhh
0.8814999999999884
checkDecisionString; bullish


             y_pred
2023-07-14  146.967
hhh
hhh
0.09310000000002105
checkDecisionString; bearish


...

              y_pred
2023-12-25  501.1475
hhh
hhh
12.847499999999968
checkDecisionString; n/a


              y_pred
2023-12-26  486.1127
hhh
hhh
-2.1872999999999934
checkDecisionString; n/a


              y_pred
2023-12-27  479.1818
hhh
hhh
-13.60820000000001
checkDecisionString; bullish


              y_pred
2023-12-28  502.0994
hhh
hhh
7.929399999999987
checkDecisionString; bullish


              y_pred
2023-12-29  493.8002
hhh
hhh
-1.4198000000000093
checkDecisionString; bullish
file saved as NVDA.csv
85.54913294797689


In [21]:

print(large)

[92.52873563218391]
